In [1]:
import pipeline
import settings
from sqlalchemy import create_engine
import pandas as pd
import datetime as dt
import api
import table_schema as ts
import db_operation as db
import numpy as np
import utils
import hvplot.pandas  # noqa
pd.options.plotting.backend = 'holoviews'
db_url = 'sqlite:///instance/local.db'

In [2]:
%load_ext autoreload
%autoreload 2

In [10]:
pipeline.left_fill_benchmark_profile()

In [11]:
pipeline.right_fill_bechmark_profile()

In [12]:
benchmark_df = db.get_all_benchmark_profile()


In [16]:
benchmark_df

date  weight display_name       ticker  \
0   2023-07-31   0.345         中国宝安  000009.XSHE   
1   2023-07-31   0.122          南玻A  000012.XSHE   
2   2023-07-31   0.264          深科技  000021.XSHE   
3   2023-07-31   0.060         招商港口  001872.XSHE   
4   2023-07-31   0.142         深圳能源  000027.XSHE   
..         ...     ...          ...          ...   
495 2023-07-31   0.085         天岳先进  688234.XSHG   
496 2023-07-31   0.041         南网科技  688248.XSHG   
497 2023-07-31   0.040         中复神鹰  688295.XSHG   
498 2023-07-31   0.182         拓荆科技  688072.XSHG   
499 2023-07-31   0.078         首创证券  601136.XSHG   

                                                sector aggregate_sector  name  
0                     电气设备I 电池II 电池化学品III 综合 工业集团企业 工业               工业  ZGBA  
1                 建筑材料I 玻璃制造II 玻璃制造III 非金属矿物制品业 玻璃 原材料            原料与能源   NBA  
2    电子I 电子制造II 消费电子零部件及组装III 计算机、通信和其他电子设备制造业 安防设备...            信息与通信   SKJ  
3                       交通运输I 航运港口II 港口III 水上运输业 港口 工业               工业  ZSGK  
4                 公用事业I 电力II 火电III 电力、热力生产和供应业 火电 公用事业             公用事业  SZNY  
..                                                 ...              ...   ...  
495     电子I 半导体II 半导体材料III 计算机、通信和其他电子设备制造业 半导体材料 信息技术            信息与通信  TYXJ  
496             电气设备I 电网设备II 电网自动化III 专业技术服务业 电网自动化 工业               工业  NWKJ  
497             化工I 化学纤维II 其他纤维III 化学纤维制造业 氨纶及其他化纤 原材料            原料与能源  ZFSY  
498              电子I 半导体II 半导体设备III 专用设备制造业 半导体设备 信息技术            信息与通信  TJKJ  
499                    非银金融I 证券II 证券III 资本市场服务 证券公司 金融            金融与地产  SCZQ  

[500 rows x 7 columns]

In [15]:
benchmark_df.hvplot.line(x='date',y='weight',by='ticker')

KeyboardInterrupt: 

In [3]:
# unique ticker list
portfolio_p = db.get_all_portfolio_profile()
ticker_list = portfolio_p['ticker'].unique().tolist()
price_df = db.get_stocks_price(ticker_list)

portfolio_p = db.get_all_portfolio_profile()
## temperaraly handle rename date to time
portfolio_p.rename(columns={'date': 'time','weight':'ini_w'}, inplace=True)

In [4]:
price_df.hvplot.line(x='time', y='close', by='ticker', width=1000, height=400)

:NdOverlay   [ticker]
   :Curve   [time]   (close)

In [5]:
def _uniformize_time_series(profile_df):
    '''
    a helper function to create analytic_df 
    
    make each entry in the time series has the same dimension
    by filling none holding stock that was held in previous period has 0 shares and 0 ini_w

    Parameters
    ----------
    profile_df : dataframe
        portfolio profile dataframe or benchmark profile dataframe
    
    Returns
    -------
    dataframe
        dataframe with uniformized time series
    '''
    # Get unique time periods
    time_periods = profile_df['time'].unique()
    time_periods = sorted(time_periods)

    # Iterate through time periods
    for i in range(len(time_periods) - 1):
        current_period = time_periods[i]
        next_period = time_periods[i + 1]
        
        current_df = profile_df[profile_df['time'] == current_period]
        next_df = profile_df[profile_df['time'] == next_period]
        
        tickers_current = current_df['ticker']
        tickers_next = next_df['ticker']
        
        # row that has ticker not in tickers_next
        missing_tickers = current_df[~tickers_current.isin(tickers_next)].copy()
        
        if len(missing_tickers) != 0:
            missing_tickers.time = next_period
            missing_tickers.shares = 0
            missing_tickers.ini_w = 0
            profile_df = pd.concat([profile_df, missing_tickers], ignore_index=True)
    # reset index
    return profile_df.reset_index(drop=True)


In [6]:
# create a merged_df 
def create_analytic_df(price_df, profile_df):
    '''
    create a df for analysis processing


    '''
    uni_profile_df = _uniformize_time_series(profile_df)
    #TODO handle rename column here
    df = price_df.merge(uni_profile_df, on=['ticker','time'], how='outer')
    df.sort_values(by=['ticker','time'], inplace=True)
    # add sector, aggregate_sector, display_name and name to missing rows
    grouped = df.groupby('ticker')
    df['sector'] = grouped['sector'].fillna(method='ffill')
    df['aggregate_sector'] = grouped['aggregate_sector'].fillna(method='ffill')
    df['display_name'] = grouped['display_name'].fillna(method='ffill')
    df['name'] = grouped['name'].fillna(method='ffill')

    # assign missing ini_w
    df['ini_w'] = grouped['ini_w'].fillna(method='ffill')
    # assign missing shares
    df['shares'] = grouped['shares'].fillna(method='ffill')
    # remove profile and price entry before first profile entry from df
    df.dropna(subset=['ini_w'], inplace=True)
    df.dropna(subset=['close'], inplace=True)
    # remove where weight is 0
    df = df[df['shares'] != 0].copy()
    return df


In [14]:
def calculate_weight_using_cash(df):
    '''
    patch df with current weight for each entry
    use cash to calculate weight
    
    Parameters
    ----------
    df : dataframe
        dataframe with processed cash column
    
    '''
    df['cur_w'] = float('nan')
    grouped = df.groupby('time')
    df.cur_w = grouped.cash.transform(lambda x: x / x.sum())

    

In [15]:
def calculate_cash(df):
    '''
    patch df with cash column
    cash = shares * close
    
    Parameters
    ----------
    df : dataframe
        dataframe with processed shares and close column
    '''
    df['cash'] = df['shares'] * df['close']

In [ ]:
def calculate_return(df, start, end):
    '''
    calculate cumulative return for each entry in the df
    '''
    selected_df = df[df.time.between(start, end)].copy()
    if len(selected_df) == 0:
        return selected_df
    selected_df.sort_values(by=['time'], inplace=True)
    selected_df['return'] = selected_df.groupby('ticker')

In [12]:
# merged_df is sorted on time
analytic_df = create_analytic_df(price_df, portfolio_p)
calculate_cash(analytic_df)
calculate_weight_using_cash(analytic_df)
# analytic_df['pct'] = analytic_df.groupby('ticker')['close'].pct_change()
# calculate weight
# calculate_weight(analytic_df)
analytic_df.hvplot.line(x='time', y='cur_w', by='ticker', width=500, height=400)
# analytic_d

:NdOverlay   [ticker]
   :Curve   [time]   (cur_w)

In [13]:
analytic_df

time       ticker    open   close    high     low       volume  \
111 2023-08-14  000877.XSHE    8.35    8.40    8.44    8.26    7357900.0   
112 2023-08-15  000877.XSHE    8.42    8.42    8.45    8.30    6000000.0   
45  2023-08-14  002202.XSHE   10.73   10.79   10.84   10.61   11395130.0   
46  2023-08-15  002202.XSHE   10.80   10.70   10.81   10.64    8332232.0   
89  2023-08-14  002271.XSHE   28.02   28.65   29.13   27.56   25064704.0   
90  2023-08-15  002271.XSHE   28.75   28.93   29.00   28.16   23813851.0   
1   2023-08-14  300408.XSHE   32.00   31.98   32.38   31.81    4754694.0   
2   2023-08-15  300408.XSHE   31.90   31.73   32.50   31.33    7131360.0   
100 2023-08-14  300413.XSHE   32.50   33.27   33.32   32.37    6601139.0   
101 2023-08-15  300413.XSHE   33.27   32.25   33.30   32.01   10558410.0   
56  2023-08-14  300759.XSHE   28.93   29.34   29.45   28.55   22129995.0   
57  2023-08-15  300759.XSHE   29.26   29.00   29.35   28.39   19712233.0   
78  2023-08-14  300979.XSHE   51.95   53.40   53.46   51.28    1051877.0   
79  2023-08-15  300979.XSHE   53.35   53.49   53.89   52.66     750046.0   
12  2023-08-14  600600.XSHG   95.00   95.00   95.35   93.20    4552721.0   
13  2023-08-15  600600.XSHG   95.03   94.04   95.35   93.51    3148755.0   
23  2023-08-14  600809.XSHG  222.00  224.27  224.68  219.23    4829616.0   
24  2023-08-15  600809.XSHG  224.25  224.00  225.58  221.00    3278697.0   
25  2023-08-16  600809.XSHG  222.60  225.50  227.59  222.22    3892264.0   
26  2023-08-17  600809.XSHG  224.46  229.72  229.95  223.28    4458965.0   
27  2023-08-18  600809.XSHG  229.78  225.76  232.10  225.40    3357055.0   
28  2023-08-21  600809.XSHG  225.00  226.85  230.68  221.00    4344149.0   
29  2023-08-22  600809.XSHG  227.39  226.45  228.20  222.26    3972474.0   
67  2023-08-14  601318.XSHG   48.30   48.53   48.82   48.28   60472146.0   
68  2023-08-15  601318.XSHG   48.52   48.68   49.08   48.02   52183684.0   
69  2023-08-16  601318.XSHG   48.32   48.35   48.94   48.13   47660376.0   
70  2023-08-17  601318.XSHG   48.01   47.91   48.18   47.33   59827368.0   
71  2023-08-18  601318.XSHG   47.90   47.52   49.00   47.52   63666255.0   
72  2023-08-21  601318.XSHG   47.40   46.67   47.49   46.67   62808090.0   
73  2023-08-22  601318.XSHG   46.90   47.00   47.30   46.47   51849548.0   
34  2023-08-14  603000.XSHG   29.00   32.19   32.19   28.85   97674615.0   
35  2023-08-15  603000.XSHG   32.83   32.46   33.51   32.02  107039840.0   
36  2023-08-16  603000.XSHG   32.46   32.46   33.33   30.90   96472064.0   
37  2023-08-17  603000.XSHG   32.04   33.80   34.22   31.83  110222658.0   
38  2023-08-18  603000.XSHG   33.50   34.20   35.15   32.80  112988265.0   
39  2023-08-21  603000.XSHG   33.16   33.17   34.66   32.16   79040908.0   
40  2023-08-22  603000.XSHG   33.87   36.49   36.49   33.77  122393536.0   
122 2023-08-14  603288.XSHG   43.50   43.31   43.77   42.63   17442281.0   
123 2023-08-15  603288.XSHG   43.60   42.73   43.60   42.40   10364699.0   
124 2023-08-16  603288.XSHG   42.43   42.49   42.91   42.40    7427002.0   
125 2023-08-17  603288.XSHG   42.20   42.73   42.83   41.71   12749545.0   
126 2023-08-18  603288.XSHG   42.65   41.35   42.65   41.28   12081279.0   
127 2023-08-21  603288.XSHG   41.35   40.60   41.47   40.60   13034690.0   
128 2023-08-22  603288.XSHG   40.65   40.49   41.07   39.90   15421643.0   
129 2023-08-23  603288.XSHG   40.49   39.83   40.53   39.80   11035245.0   
130 2023-08-24  603288.XSHG   39.92   40.28   40.50   39.52   12865543.0   
131 2023-08-25  603288.XSHG   40.08   40.08   40.55   39.91    8887682.0   

            money   shares                                             sector  \
111  6.138507e+07   1100.0           建筑材料I 水泥制造II 水泥制造III 非金属矿物制品业 水泥与混凝土 原材料   
112  5.030405e+07   1100.0           建筑材料I 水泥制造II 水泥制造III 非金属矿物制品业 水泥与混凝土 原材料   
45   1.222121e+08   1200.0               电气设备I 风电设备II 风电整机III 通用设备制造业 风电设备 工业   
46   8.922860e+07   1200.0           